Get Period BS function

In [ ]:
def GetPeriodsBS(S_i,Pshort,Plong,thr_bs,thr_nbs):
    #Analyse S2 - START period
    START_BS = 'nan'
    END_BS = 'nan'
    Conf_BS = np.nan
    M1 = 0
    M2 = np.nan
    M3 = np.nan
    M4 = np.nan
    M5 = np.nan
    M6 = np.nan
    NbrBS = np.nan
    NbrTT = 0
    EndLook = False
    LookNext = False
    ind = S_i.index
    M3_transition = 0
    baresoil_lastdate = 'nan'

    for idx in ind:
        NbrTT += 1 
        # look for START_BS

        if (np.isnan(M1)| (M1==0)) & (S_i.at[idx,'pred']=='BS') & (S_i.at[idx,'conf']>=thr_bs):
            M1 = 1
            START_BS = S_i.at[idx,'dates']
            NbrBS = 0
            d_start = datetime.strptime(START_BS,'%Y-%m-%d')
            continue
        elif (M1 != 1):
            d_start = datetime.strptime(f'{year}-01-01','%Y-%m-%d')

        d_continue = datetime.strptime(S_i.at[idx,'dates'],'%Y-%m-%d')
        
        if (M1 == 1) & (d_continue-d_start > Pshort) & (END_BS=='nan') & (M2 == 0):
            END_BS = START_BS
            EndLook = False
            LookNext = True
        elif (M1 == 1) & (d_continue-d_start > Plong) & (END_BS=='nan') & (M4==0) & (baresoil_lastdate != 'nan'):
            END_BS = baresoil_lastdate
            EndLook = False
            LookNext = True

        elif (M1==1) and (END_BS=='nan'):
            NbrBS += 1
            if np.isnan(M2):
                M2 = 0
                M3 = 0
            if (S_i.at[idx,'pred']=='BS'):
                EndLook = True
                M4 = 0
                baresoil_lastdate = 'nan'
                M3_transition = 0

            if (S_i.at[idx,'conf'] > thr_bs) & (S_i.at[idx,'pred']=='BS') :
                M2 += 1
                M3 += 2
            
            elif (S_i.at[idx,'pred']=='BS') & (S_i.at[idx,'conf'] <= thr_bs) :
                M3 += 1

            elif ((S_i.at[idx,'pred']!='BS') & (S_i.at[idx,'conf'] <= thr_nbs)): 
                M3 += -2
                M3_transition += 2
                if baresoil_lastdate=='nan':
                    baresoil_lastdate = S_i.at[idx-1,'dates']
                       

        # look for the END_BS

        if (M1==1) & (EndLook) :
            LookNext = True
            if (M4==0) & (S_i.at[idx,'pred']!='BS') & (S_i.at[idx,'conf']> thr_nbs):
                M4 = 1
                if baresoil_lastdate=='nan':
                    END_BS = S_i.at[idx-1,'dates']
                    
                else:
                    END_BS = baresoil_lastdate
                    M3 += M3_transition
                    NbrBS += - M3_transition/2

                d_end = datetime.strptime(END_BS,'%Y-%m-%d')
                    
                continue
            elif (M4!=1):
                M4 = 0
                d_end = d_start

            if (M4==1) & (d_continue-d_end < Plong):
                if np.isnan(M5):
                    M5 = 0
                    M6 = 0
                if (S_i.at[idx,'conf']>thr_nbs) & (S_i.at[idx,'pred']!='BS') :
                    M5 += 1
                    M6 += 2
                elif (S_i.at[idx,'conf']<= thr_nbs) & (S_i.at[idx,'pred']!='BS'):
                    M6 += 1
                elif (S_i.at[idx,'pred']=='BS') & (S_i.at[idx,'conf']>thr_bs) & (d_continue-d_end < Pshort):
                    M6 += -2
                    #print('end_next')
                    if M6 <= -4 :
                        M4 = 0
                        END_BS = 'nan'
                        continue
                elif (S_i.at[idx,'pred']=='BS'):
                    M6 += -2
                else : 
                    M6 += 0

        #print(d_continue)
        #print(START_BS)
        #print('M2: ' + str(M2))
        #print('M3: ' + str(M3))
        #print('M3_t: ' + str(M3_transition))
        #print(END_BS)
        #print(M6)
        #print(baresoil_lastdate)

    if ((M2 >= 1) & (M4 == 0) & (baresoil_lastdate=='nan')):
        END_BS = 'Continue'
        LookNext = False
    elif (baresoil_lastdate!='nan'):
        END_BS = baresoil_lastdate

    if (END_BS=='nan'):
        Conf_BS = 'nan'
# according to the value of M1-M3 --> assess the confidence start and the start_date
 
    if (M2 == 0) & (np.isnan(M4) | (M4 == 0)) :
        END_BS = START_BS

    if (M1 == 1) & (M2 >= 3) & (M3 >= 2) & (M6 > 0):
        Conf_BS = 'Strong'
    
    elif (M1 == 1) & (M2 > 0) & (M3 >= 0) & (M5>0):
        Conf_BS = 'Good'
    
    elif (M1 == 1) & (M2 > 0) & (M3 >= 0):
        Conf_BS = 'Medium'

    elif ((M1==1) & (M2 == 0) & (M3 >= 0)) | ((M2 >= 0) & (M3 <=0)):
        Conf_BS = 'Poor'

    if (M1==1) & (M3 < 0) & (END_BS == START_BS):
        Conf_BS = 'Doubtful'
        
    

# set the END date if M1 not confirm and END date note found 
        
    return(M1,M2,M3,M4,M5,M6,START_BS,END_BS,Conf_BS,NbrBS,LookNext,NbrTT)

Output Markers function

In [ ]:
def OutputMarkers(Sat,NPeriod,df_results,i,Pshort,Plong,thr_bs,thr_nbs):
    for p in range(1,NPeriod+1):
        if p == 1:
            S2_i = df_results.loc[df_results.NewID==i]
            markers = list(GetPeriodsBS(S_i=S2_i,Pshort=Pshort,Plong=Plong,thr_bs=thr_bs,thr_nbs=thr_nbs))
            NbrTT = markers[11]
            LastObs = lambda x: np.nan if x.empty else x.iloc[-1]['dates']
            df_out1 = {
            'NewID' : i,
            f'NbrTT{Sat}' : NbrTT,
            f'LastObs{Sat}': LastObs(S2_i),
            f'M1_{Sat}_{p}' : markers[0],
            f'M2_{Sat}_{p}' : markers[1],
            f'M3_{Sat}_{p}' : markers[2],
            f'M4_{Sat}_{p}' : markers[3],
            f'M5_{Sat}_{p}' : markers[4],
            f'M6_{Sat}_{p}' : markers[5],
            f'STARTBS_{Sat}_{p}' : markers[6],
            f'ENDBS_{Sat}_{p}' : markers[7],
            f'Conf_{Sat}_{p}' : markers[8],
            f'Nbr{Sat}BS_{p}' : markers[9],
            f'Look_next{Sat}_{p}' : markers[10]
            }

        else :
            if markers[10]:
                S2_i2 = df_results.loc[(df_results.NewID==i) & (df_results.date_d > (datetime.strptime(markers[7],'%Y-%m-%d') + Period_c1))]
                markers = list(GetPeriodsBS(S2_i2,Pshort,Plong,thr_bs,thr_nbs))
            else:
                S2_i2 = df_results.head(0)
                markers = list(GetPeriodsBS(S2_i2,Pshort,Plong,thr_bs,thr_nbs))

            df_out1.setdefault(f'M1_{Sat}_{p}',markers[0])
            df_out1.setdefault(f'M2_{Sat}_{p}',markers[1])
            df_out1.setdefault(f'M3_{Sat}_{p}',markers[2])
            df_out1.setdefault(f'M4_{Sat}_{p}',markers[3])
            df_out1.setdefault(f'M5_{Sat}_{p}',markers[4])
            df_out1.setdefault(f'M6_{Sat}_{p}',markers[5])
            df_out1.setdefault(f'STARTBS_{Sat}_{p}',markers[6])
            df_out1.setdefault(f'ENDBS_{Sat}_{p}',markers[7])
            df_out1.setdefault(f'Conf_{Sat}_{p}',markers[8])
            df_out1.setdefault(f'Nbr{Sat}BS_{p}',markers[9])
            df_out1.setdefault(f'Look_next{Sat}_{p}',markers[10])

    
    return(df_out1)

Improve S2 conf with S1 function

In [ ]:
def S1_S2_comparaison_and_countdays(i,dti_S2,dti_S1,NPeriodS2,NPeriodS1):
    tt_daysS2=np.nan
    tt_daysS1=np.nan
    tt_daysS1S2 = np.nan
    dti_S2 = dti_S2.reset_index()
    dti_S1 = dti_S1.reset_index()
    ending = lambda x,s,t: datetime.strptime(x.loc[0,f'LastObs{s}'],'%Y-%m-%d') if x.loc[0,f'ENDBS_{s}_{t}'] in ('Continue','nan') else datetime.strptime(x.loc[0,f'ENDBS_{s}_{t}'],'%Y-%m-%d')
    delta_zero = lambda x: 0 if x < 0 else x
    periodsS2_out = []
    periodsS1_out = []
    
    if NPeriodS2!= 0 :
        tt_daysS2 = 0
        NbrS2TT = dti_S2.loc[0,'NbrTTS2']
        LastObsS2 = dti_S2.loc[0,'LastObsS2']
        if NPeriodS1 == 0:

            for p in range(1,NPeriodS2+1):
                periodsS2_out.append(dti_S2.loc[0,f'STARTBS_S2_{p}'])
                periodsS2_out.append(dti_S2.loc[0,f'ENDBS_S2_{p}'])
                periodsS2_out.append(dti_S1.loc[0,f'Conf_S2_{p1}'])
                if dti_S2.loc[0,f'M1_S2_{p}'] == 1:
                    deltaS2 =  ending(dti_S2,'S2',p) - datetime.strptime(dti_S2.loc[0,f'STARTBS_S2_{p}'],'%Y-%m-%d')
                    if deltaS2.days == 0:
                        tt_daysS2 += 1
                    else:
                        tt_daysS2 += deltaS2.days
        
        else:
            tt_daysS1S2 = 0
            for p in range(1,NPeriodS2+1):
                periodsS2_out.append(dti_S2.loc[0,f'STARTBS_S2_{p}'])
                periodsS2_out.append(dti_S2.loc[0,f'ENDBS_S2_{p}'])
                Conf_S2 = dti_S2.loc[0,f'Conf_S2_{p}']
                if dti_S2.loc[0,f'M1_S2_{p}'] == 1:
                        deltaS2 =  ending(dti_S2,'S2',p) - datetime.strptime(dti_S2.loc[0,f'STARTBS_S2_{p}'],'%Y-%m-%d')
                        if deltaS2.days == 0:
                            tt_daysS2 += 1
                        else:
                            tt_daysS2 += deltaS2.days
                for p1 in range(1,NPeriodS1+1):
                    if (dti_S2.loc[0,f'M1_S2_{p}'] == 1) & (dti_S1.loc[0,f'M1_S1_{p1}'] == 1):
                        startS2 = datetime.strptime(dti_S2.loc[0,f'STARTBS_S2_{p}'],'%Y-%m-%d')
                        startS1 = datetime.strptime(dti_S1.loc[0,f'STARTBS_S1_{p1}'],'%Y-%m-%d')
                        start = max(startS2,startS1)
                        end = min(ending(dti_S2,'S2',p),ending(dti_S1,'S1',p1))
                        delta =  end - start
                        #print(delta)
                        tt_daysS1S2 += delta_zero(delta.days)
                        #print('tt_daysS1S2 : ',tt_daysS1S2)
                        if delta.days > 0:
                            Conf_S2 = niv_Conf[niv_Conf.index(dti_S2.loc[0,f'Conf_S2_{p}'])+1]+'_S1'
                periodsS2_out.append(Conf_S2)
                
    if NPeriodS1!= 0 :
        tt_daysS1 = 0
        NbrS1TT = dti_S1.loc[0,'NbrTTS1']
        LastObsS1 = dti_S1.loc[0,'LastObsS1']
        for p1 in range(1,NPeriodS1+1):
            periodsS1_out.append(dti_S1.loc[0,f'STARTBS_S1_{p1}'])
            periodsS1_out.append(dti_S1.loc[0,f'ENDBS_S1_{p1}'])
            periodsS1_out.append(dti_S1.loc[0,f'Conf_S1_{p1}'])
            if dti_S1.loc[0,f'M1_S1_{p1}'] == 1:
                deltaS1 =  ending(dti_S1,'S1',p1) - datetime.strptime(dti_S1.loc[0,f'STARTBS_S1_{p1}'],'%Y-%m-%d')
                #print(delta)
                if deltaS1.days == 0:
                    tt_daysS1 += 1
                else:
                    tt_daysS1 += deltaS1.days

    
    return(i,*periodsS2_out,NbrS2TT,LastObsS2,tt_daysS2,tt_daysS1S2,*periodsS1_out,NbrS1TT,LastObsS1,tt_daysS1)